- /l/users/fathinah.izzati/coco-mulla-repo/video-enc
- /l/users/fathinah.izzati/coco-mulla-repo/audio_enc.ipynb
- /l/users/fathinah.izzati/coco-mulla-repo/main_v3.ipynb


- /l/users/fathinah.izzati/coco-mulla-repo/demo/output/tnj_test

In [1]:
from coco_mulla.data_loader.dataset_sampler import Dataset, collate_fn
import torch
from config import TrainCfg
import os
from coco_mulla.models import CoCoMulla
import torch.nn as nn

dataset = Dataset(
    rid=0, # No distributed rank needed
    path_lst=['/l/users/fathinah.izzati/coco-mulla-repo/test2.lst'],
    sampling_prob=None,
    sampling_strategy='prob-based',
    cfg=TrainCfg)

dataloader = torch.utils.data.DataLoader(
    dataset,
    batch_size=TrainCfg.batch_size,
    collate_fn=collate_fn,
    shuffle=False,
    num_workers=0,
    # sampler=DistributedSampler(dataset),
    pin_memory=True,
    drop_last=True)

/home/fathinah.izzati/miniconda3/envs/cocomulla/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


0 /l/users/fathinah.izzati/coco-mulla-repo/test2.lst
num of files 29


In [2]:
learning_rate = 0.05
num_layers= 48
latent_dim = 512
device = "cuda"
model = CoCoMulla(TrainCfg.sample_sec, num_layers=num_layers, latent_dim=latent_dim).to(device)
model.set_training()

model_dir ="/l/users/fathinah.izzati/coco-mulla-repo/expe/new_experiment"
if not os.path.exists(model_dir):
    os.mkdir(model_dir)

/home/fathinah.izzati/miniconda3/envs/cocomulla/lib/python3.11/site-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


load....musicgen bk
lm_bk, here
cp_transformer.masked_embedding
cp_transformer.pos_emb
cp_transformer.gates
cp_transformer.encodec_emb.weight
cp_transformer.merge_linear.0.weight
cp_transformer.merge_linear.1.weight
cp_transformer.merge_linear.2.weight
cp_transformer.merge_linear.3.weight
cp_transformer.merge_linear.4.weight
cp_transformer.merge_linear.5.weight
cp_transformer.merge_linear.6.weight
cp_transformer.merge_linear.7.weight
cp_transformer.merge_linear.8.weight
cp_transformer.merge_linear.9.weight
cp_transformer.merge_linear.10.weight
cp_transformer.merge_linear.11.weight
cp_transformer.merge_linear.12.weight
cp_transformer.merge_linear.13.weight
cp_transformer.merge_linear.14.weight
cp_transformer.merge_linear.15.weight
cp_transformer.merge_linear.16.weight
cp_transformer.merge_linear.17.weight
cp_transformer.merge_linear.18.weight
cp_transformer.merge_linear.19.weight
cp_transformer.merge_linear.20.weight
cp_transformer.merge_linear.21.weight
cp_transformer.merge_linear.22.w

In [3]:
import numpy as np
from torch.utils.tensorboard import SummaryWriter
from coco_mulla.utilities.trainer_utils import Trainer
from tqdm import tqdm
def loss_fn(outputs, y):
    prob = outputs.logits
    mask = outputs.mask
    prob = prob[mask]
    y = y[mask]
    prob = prob.view(-1, 2048)
    return nn.CrossEntropyLoss()(prob, y)


def train(model, dataset, dataloader, device, model_dir, learning_rate):
    # optimizer and lr scheduler
    num_steps = len(dataloader)
    epochs = TrainCfg.epoch
    rng = np.random.RandomState(569)
    writer = SummaryWriter(model_dir, flush_secs=20)

    trainer = Trainer(params=model.parameters(), lr=learning_rate, num_epochs=epochs, num_steps=num_steps)

    model = model.to(device)
    step = 0
    for e in range(0, epochs):
        mean_loss = 0
        n_element = 0
        model.train()

        dl = tqdm(dataloader, desc=f"Epoch {e}")
        r = rng.randint(0, 233333)
        dataset.reset_random_seed(r, e)
        for i, batch in enumerate(dl):
            desc = batch["desc"]

            music = batch["music"].to(device).long()
            video = batch["video"].to(device).float()



            batch_1 = {
                "music": music,
                "video": video,
                "desc": desc,

            }
            # with autocast:
            outputs = model(**batch_1)
            print("==========================================")
            print(outputs)
            
            r_loss = loss_fn(outputs, music)

            grad_1, lr_1 = trainer.step(r_loss, model.parameters())

            step += 1
            n_element += 1
            writer.add_scalar("r_loss", r_loss.item(), step)
            writer.add_scalar("grad_1", grad_1, step)
            writer.add_scalar("lr_1", lr_1, step)

            mean_loss += r_loss.item()

        mean_loss = mean_loss / n_element
        with torch.no_grad():
            writer.add_scalar('train/mean_loss', mean_loss, step)
            model.save_weights(os.path.join(model_dir, f"diff_{e}_end.pth"))

In [4]:
train(model, dataset, dataloader, device, model_dir, learning_rate)

Epoch 0:   0%|          | 0/29 [00:00<?, ?it/s]

music (4, 500)
video (501, 512)
video torch.Size([1, 501, 512])
B 1
T 501
o torch.Size([1, 501, 2048])
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6.1293e-01,
           6.0278e-02,  1.0372e-01],
         [ 2.3717e-01,  2.5061e-01,  4.6139e-02,  ...,  5.6958e-01,
           5.5856e-02,  1.0088e-01],
         [ 2.8362e-01,  2.3239e-01,  5.4547e-02,  ...,  5.3265e-01,
           5.2897e-02,  9.9723e-02],
         ...,
         [ 3.8433e-01,  1.1270e-01,  1.9521e-01,  ...,  1.7201e-02,
           1.2753e-01,  1.0957e-02],
         [ 3.2914e-01,  1.3844e-01,  1.9777e-01,  ...,  1.5752e-02,
           7.5148e-02,  1.2785e-02],
         [ 2.5572e-01,  1.9021e-01,  1.9912e-01,  ...,  1.3008e-02,
          -5.5511e-17,  1.4818e-02]]], device='cuda:0')
cond t shape torch.Size([1, 501, 512])
merge linear torch.Size([1, 501, 2048])
shape pos emb torch.Size([1, 501, 2048])
embedding torch.Size([1, 501, 2048])
lewat!!
masuk train
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6

/home/fathinah.izzati/miniconda3/envs/cocomulla/lib/python3.11/site-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "
Epoch 0:   3%|▎         | 1/29 [00:07<03:20,  7.15s/it]

music (4, 500)
video (501, 512)
video torch.Size([1, 501, 512])
B 1
T 501
o torch.Size([1, 501, 2048])
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6.1293e-01,
           6.0278e-02,  1.0372e-01],
         [ 2.3717e-01,  2.5061e-01,  4.6139e-02,  ...,  5.6958e-01,
           5.5856e-02,  1.0088e-01],
         [ 2.8362e-01,  2.3239e-01,  5.4547e-02,  ...,  5.3265e-01,
           5.2897e-02,  9.9723e-02],
         ...,
         [ 3.8433e-01,  1.1270e-01,  1.9521e-01,  ...,  1.7201e-02,
           1.2753e-01,  1.0957e-02],
         [ 3.2914e-01,  1.3844e-01,  1.9777e-01,  ...,  1.5752e-02,
           7.5148e-02,  1.2785e-02],
         [ 2.5572e-01,  1.9021e-01,  1.9912e-01,  ...,  1.3008e-02,
          -5.5511e-17,  1.4818e-02]]], device='cuda:0')
cond t shape torch.Size([1, 501, 512])
merge linear torch.Size([1, 501, 2048])
shape pos emb torch.Size([1, 501, 2048])
embedding torch.Size([1, 501, 2048])
lewat!!
masuk train
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6

Epoch 0:   7%|▋         | 2/29 [00:07<01:31,  3.39s/it]

...

Epoch 4:  93%|█████████▎| 27/29 [00:06<00:00,  3.96it/s]

music (4, 500)
video (501, 512)
video torch.Size([1, 501, 512])
B 1
T 501
o torch.Size([1, 501, 2048])
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6.1293e-01,
           6.0278e-02,  1.0372e-01],
         [ 2.3717e-01,  2.5061e-01,  4.6139e-02,  ...,  5.6958e-01,
           5.5856e-02,  1.0088e-01],
         [ 2.8362e-01,  2.3239e-01,  5.4547e-02,  ...,  5.3265e-01,
           5.2897e-02,  9.9723e-02],
         ...,
         [ 3.8433e-01,  1.1270e-01,  1.9521e-01,  ...,  1.7201e-02,
           1.2753e-01,  1.0957e-02],
         [ 3.2914e-01,  1.3844e-01,  1.9777e-01,  ...,  1.5752e-02,
           7.5148e-02,  1.2785e-02],
         [ 2.5572e-01,  1.9021e-01,  1.9912e-01,  ...,  1.3008e-02,
          -5.5511e-17,  1.4818e-02]]], device='cuda:0')
cond t shape torch.Size([1, 501, 512])
merge linear torch.Size([1, 501, 2048])
shape pos emb torch.Size([1, 501, 2048])
embedding torch.Size([1, 501, 2048])
lewat!!
masuk train
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6

Epoch 4:  97%|█████████▋| 28/29 [00:07<00:00,  3.96it/s]

music (4, 500)
video (501, 512)
video torch.Size([1, 501, 512])
B 1
T 501
o torch.Size([1, 501, 2048])
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6.1293e-01,
           6.0278e-02,  1.0372e-01],
         [ 2.3717e-01,  2.5061e-01,  4.6139e-02,  ...,  5.6958e-01,
           5.5856e-02,  1.0088e-01],
         [ 2.8362e-01,  2.3239e-01,  5.4547e-02,  ...,  5.3265e-01,
           5.2897e-02,  9.9723e-02],
         ...,
         [ 3.8433e-01,  1.1270e-01,  1.9521e-01,  ...,  1.7201e-02,
           1.2753e-01,  1.0957e-02],
         [ 3.2914e-01,  1.3844e-01,  1.9777e-01,  ...,  1.5752e-02,
           7.5148e-02,  1.2785e-02],
         [ 2.5572e-01,  1.9021e-01,  1.9912e-01,  ...,  1.3008e-02,
          -5.5511e-17,  1.4818e-02]]], device='cuda:0')
cond t shape torch.Size([1, 501, 512])
merge linear torch.Size([1, 501, 2048])
shape pos emb torch.Size([1, 501, 2048])
embedding torch.Size([1, 501, 2048])
lewat!!
masuk train
tensor([[[ 1.8195e-01,  2.7267e-01,  3.5422e-02,  ...,  6

Epoch 4: 100%|██████████| 29/29 [00:07<00:00,  3.97it/s]


In [1]:
import numpy as np

In [3]:
np.load('/l/users/fathinah.izzati/coco-mulla-repo/demo/output/tnj_test/segment_001/video_emb.npy').shape

(50, 512)